<a href="https://colab.research.google.com/github/laurengray42/Coursera_Capstone/blob/master/week3part2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### **PART 1**

Import BeautifulSoup
</br>
headers for spoofing a browser,</br>
look at code from url

In [1]:
from bs4 import BeautifulSoup
import requests

headers = requests.utils.default_headers()
headers.update({ 'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:52.0) Gecko/20100101 Firefox/52.0'})

url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
req = requests.get(url, headers)
soup = BeautifulSoup(req.content, 'html.parser')
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   List of postal codes of Canada: M - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgMonthNamesShort":["","Jan","Feb","Mar","Apr","May","Jun","Jul","Aug","Sep","Oct","Nov","Dec"],"wgRequestId":"Xf0DMgpAADoAAF45rfoAAABQ","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_postal_codes_of_Canada:_M","wgTitle":"List of postal codes of Canada: M","wgCurRevisionId":930529633,"wgRevisionId":930529633,"wgArticleId":539066,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Communi

Import Pandas

In [0]:
import pandas as pd
import numpy as np


search for table elements

In [0]:
table = soup.find_all('table')[0] 
df = pd.read_html(str(table))


Check df list

In [0]:
df=df[0]

In [5]:
print(df)

    Postcode           Borough          Neighbourhood
0        M1A      Not assigned           Not assigned
1        M2A      Not assigned           Not assigned
2        M3A        North York              Parkwoods
3        M4A        North York       Victoria Village
4        M5A  Downtown Toronto           Harbourfront
..       ...               ...                    ...
282      M8Z         Etobicoke              Mimico NW
283      M8Z         Etobicoke     The Queensway West
284      M8Z         Etobicoke  Royal York South West
285      M8Z         Etobicoke         South of Bloor
286      M9Z      Not assigned           Not assigned

[287 rows x 3 columns]


Convert list to a dataframe

In [0]:
import numpy as np
from numpy import array

check dataframe

In [7]:
type(df)

pandas.core.frame.DataFrame

In [8]:
df.head()

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

Remove not assigned Boroughs

In [0]:
df_filtered = df[df['Borough'] != 'Not assigned'] 

In [10]:
df_filtered.head()

Postcode           Borough     Neighbourhood
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M6A        North York  Lawrence Heights
6      M6A        North York    Lawrence Manor

In [11]:
df_filtered.shape

(210, 3)

### **PART 2**

Import Coordinates

In [0]:
coord = pd.read_csv("https://cocl.us/Geospatial_data")

In [13]:
coord.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

Combine dataframes

In [0]:
 new = df_filtered.set_index('Postcode').join(coord.set_index('Postal Code'))

In [15]:
new.head()

Borough   Neighbourhood   Latitude  Longitude
M1B  Scarborough           Rouge  43.806686 -79.194353
M1B  Scarborough         Malvern  43.806686 -79.194353
M1C  Scarborough  Highland Creek  43.784535 -79.160497
M1C  Scarborough      Rouge Hill  43.784535 -79.160497
M1C  Scarborough      Port Union  43.784535 -79.160497

check shape

In [16]:
new.shape

(210, 4)

fix index

In [0]:
newdf=new.reset_index()

In [18]:
newdf.head()

index      Borough   Neighbourhood   Latitude  Longitude
0   M1B  Scarborough           Rouge  43.806686 -79.194353
1   M1B  Scarborough         Malvern  43.806686 -79.194353
2   M1C  Scarborough  Highland Creek  43.784535 -79.160497
3   M1C  Scarborough      Rouge Hill  43.784535 -79.160497
4   M1C  Scarborough      Port Union  43.784535 -79.160497

**PART 3**

clustering</br>
import **libraries**

In [19]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

/bin/bash: conda: command not found
Libraries imported.


count boroughs

In [20]:
mycounts=newdf.groupby('Borough').count()
print(mycounts)

                  index  Neighbourhood  Latitude  Longitude
Borough                                                    
Central Toronto      17             17        17         17
Downtown Toronto     37             37        37         37
East Toronto          7              7         7          7
East York             6              6         6          6
Etobicoke            44             44        44         44
Mississauga           1              1         1          1
North York           38             38        38         38
Queen's Park          1              1         1          1
Scarborough          37             37        37         37
West Toronto         13             13        13         13
York                  9              9         9          9


In [28]:
t_grouped = newdfone.groupby('Neighborhood').mean().reset_index()
t_grouped

Neighborhood  Adelaide  Agincourt  \
0                                             Adelaide         1          0   
1                                            Agincourt         0          1   
2                                      Agincourt North         0          0   
3                                       Albion Gardens         0          0   
4                                            Alderwood         0          0   
5                                       Bathurst Manor         0          0   
6                                        Bathurst Quay         0          0   
7                                      Bayview Village         0          0   
8                                     Beaumond Heights         0          0   
9                                         Bedford Park         0          0   
10                                         Berczy Park         0          0   
11                                         Birch Cliff         0          0   
12                                   Bloordale Gardens         0          0   
13                                            Brockton         0          0   
14   Business Reply Mail Processing Centre 969 Eastern         0          0   
15                                         CFB Toronto         0          0   
16                                            CN Tower         0          0   
17                                         Cabbagetown         0          0   
18                                 Caledonia-Fairbanks         0          0   
19               Canada Post Gateway Processing Centre         0          0   
20                                           Cedarbrae         0          0   
21                                  Central Bay Street         0          0   
22                                           Chinatown         0          0   
23                                            Christie         0          0   
24                                Church and Wellesley         0          0   
25                                            Clairlea         0          0   
26                                      Clarks Corners         0          0   
27                                          Cliffcrest         0          0   
28                                           Cliffside         0          0   
29                                      Cliffside West         0          0   
30                                          Cloverdale         0          0   
31                                      Commerce Court         0          0   
32                                          Davisville         0          0   
33                                    Davisville North         0          0   
34                                           Deer Park         0          0   
35                                             Del Ray         0          0   
36                                     Design Exchange         0          0   
37                                     Don Mills North         0          0   
38                                     Don Mills South         0          0   
39                                         Dorset Park         0          0   
40                                  Dovercourt Village         0          0   
41                                           Downsview         0          0   
42                                   Downsview Central         0          0   
43                                      Downsview East         0          0   
44                                     Downsview North         0          0   
45                                 Downsview Northwest         0          0   
46                                      Downsview West         0          0   
47                                            Dufferin         0          0   
48                                East Birchmount Park         0          0   
49                                        East Toronto         0          0   
50           

In [21]:
# one hot encoding
newdfone = pd.get_dummies(newdf[['Neighbourhood']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
newdfone['Neighborhood'] = newdf['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [newdfone.columns[-1]] + list(newdfone.columns[:-1])
newdfone = newdfone[fixed_columns]

newdfone.head()

Neighborhood  Adelaide  Agincourt  Agincourt North  Albion Gardens  \
0           Rouge         0          0                0               0   
1         Malvern         0          0                0               0   
2  Highland Creek         0          0                0               0   
3      Rouge Hill         0          0                0               0   
4      Port Union         0          0                0               0   

   Alderwood  Bathurst Manor  Bathurst Quay  Bayview Village  \
0          0               0              0                0   
1          0               0              0                0   
2          0               0              0                0   
3          0               0              0                0   
4          0               0              0                0   

   Beaumond Heights  Bedford Park  Berczy Park  Birch Cliff  \
0                 0             0            0            0   
1                 0             0            0            0   
2                 0             0            0            0   
3                 0             0            0            0   
4                 0             0            0            0   

   Bloordale Gardens  Brockton  \
0                  0         0   
1                  0         0   
2                  0         0   
3                  0         0   
4                  0         0   

   Business Reply Mail Processing Centre 969 Eastern  CFB Toronto  CN Tower  \
0                                                  0            0         0   
1                                                  0            0         0   
2                                                  0            0         0   
3                                                  0            0         0   
4                                                  0            0         0   

   Cabbagetown  Caledonia-Fairbanks  Canada Post Gateway Processing Centre  \
0            0                    0                                      0   
1            0                    0                                      0   
2            0                    0                                      0   
3            0                    0                                      0   
4            0                    0                                      0   

   Cedarbrae  Central Bay Street  Chinatown  Christie  Church and Wellesley  \
0          0                   0          0         0                     0   
1          0                   0          0         0                     0   
2          0                   0          0         0                     0   
3          0                   0          0         0                     0   
4          0                   0          0         0                     0   

   Clairlea  Clarks Corners  Cliffcrest  Cliffside  Cliffside West  \
0         0               0           0          0               0   
1         0               0           0          0               0   
2         0               0           0          0               0   
3         0               0           0          0               0   
4         0               0           0          0               0   

   Cloverdale  Commerce Court  Davisville  Davisville North  Deer Park  \
0           0               0           0                 0          0   
1           0               0           0                 0          0   
2           0               0           0                 0          0   
3           0               0           0                 0          0   
4           0               0           0                 0          0   

   Del Ray  Design Exchange  Don Mills North  Don Mills South  Dorset Park  \
0        0                0                0                0            0   
1        0                0                0                0            0   
2        0                0                0                0     

In [22]:
newdfone.shape

(210, 209)

In [23]:
newdf_grouped = newdfone.groupby('Neighborhood').mean().reset_index()
newdf_grouped

Neighborhood  Adelaide  Agincourt  \
0                                             Adelaide         1          0   
1                                            Agincourt         0          1   
2                                      Agincourt North         0          0   
3                                       Albion Gardens         0          0   
4                                            Alderwood         0          0   
5                                       Bathurst Manor         0          0   
6                                        Bathurst Quay         0          0   
7                                      Bayview Village         0          0   
8                                     Beaumond Heights         0          0   
9                                         Bedford Park         0          0   
10                                         Berczy Park         0          0   
11                                         Birch Cliff         0          0   
12                                   Bloordale Gardens         0          0   
13                                            Brockton         0          0   
14   Business Reply Mail Processing Centre 969 Eastern         0          0   
15                                         CFB Toronto         0          0   
16                                            CN Tower         0          0   
17                                         Cabbagetown         0          0   
18                                 Caledonia-Fairbanks         0          0   
19               Canada Post Gateway Processing Centre         0          0   
20                                           Cedarbrae         0          0   
21                                  Central Bay Street         0          0   
22                                           Chinatown         0          0   
23                                            Christie         0          0   
24                                Church and Wellesley         0          0   
25                                            Clairlea         0          0   
26                                      Clarks Corners         0          0   
27                                          Cliffcrest         0          0   
28                                           Cliffside         0          0   
29                                      Cliffside West         0          0   
30                                          Cloverdale         0          0   
31                                      Commerce Court         0          0   
32                                          Davisville         0          0   
33                                    Davisville North         0          0   
34                                           Deer Park         0          0   
35                                             Del Ray         0          0   
36                                     Design Exchange         0          0   
37                                     Don Mills North         0          0   
38                                     Don Mills South         0          0   
39                                         Dorset Park         0          0   
40                                  Dovercourt Village         0          0   
41                                           Downsview         0          0   
42                                   Downsview Central         0          0   
43                                      Downsview East         0          0   
44                                     Downsview North         0          0   
45                                 Downsview Northwest         0          0   
46                                      Downsview West         0          0   
47                                            Dufferin         0          0   
48                                East Birchmount Park         0          0   
49                                        East Toronto         0          0   
50           

In [24]:
newdf_grouped.shape

(208, 209)

So I am stuck, hopefully submitting this, someone would tell me where i went wrong.